# * * * LINEAR ALGEBRA AND BALL ARITHMETIC * * *

## Gauss-Jordan elimination

In [4]:
def reduce (mat) :
    
    """
    Transform the input matrix into a reduced matrix using a Gauss method adapted to
    ball arithmetic, regarding balls containing zero as exact zeros.
    
    INPUT:
     -- ''mat'' -- ball matrix.
    
    OUTPUT:
     -- ''rank'' -- integer.
    
    """
    
    nrows, ncols = mat.dimensions()
    rank = 0 # minimal rank = number of used pivots
    
    P = []
    
    for j in range (ncols) :
        
        # finding a good pivot in the column
        zero_column = True
        maximum = 0.
        for i in range(rank, nrows) :
            mij = mat[i,j]
            if not mij.contains_zero() :
                zero_column = False
                tmp = abs(mij.mid()) - mij.rad()
                if tmp > maximum :
                    pivot_row = i
                    maximum = tmp
        
        if not zero_column :
            
            # moving the selected row to the beginning
            mat[rank], mat[pivot_row] = mat[pivot_row], mat[rank]
            
            # normalizing the row with pivot = 1
            pivot = mat[rank,j]
            v = vector(mat[rank])/pivot
            mat[rank] = list(v)
            mat[rank,j] = 1
            
            # putting zeros over and under the pivot
            for i in range(nrows) :
                if not i == rank :
                    vi = vector(mat[i])
                    x = vi[j]
                    mat[i] = list(vi - x * v)
                    mat[i,j] = 0
            
            rank = rank + 1
    
    return rank

## Computing $\text{Inv}_{\mathcal{M}}(v)$

In [5]:
def Inv (Ms, v) :
    
    """
    Compute the smallest subspace containing the vector v
    and invariant by each matrix of Ms.
    
    INPUT:
     -- ''Ms'' -- a list of ball matrices.
     -- ''v'' -- a ball vector.
    
    OUTPUT:
     -- ''E'' -- a list of ball vectors.
    
    Note: It is possible that a particular choice of point
    matrices and point vectors provides a subspace greater 
    than the computed subspace.
    
    """
    
    E = [v]
    old_dim, dim = 0, 1
    
    while old_dim < dim :
        
        # matrix-vector multiplications 
        E.extend([M*u for M in Ms for u in E])
        
        # echelonizing and removing null vectors
        mat = matrix(E)
        r = reduce(mat)
        E = list(mat[:r])
        
        old_dim, dim = dim, r
    
    return E